In [47]:
import pandas as pd
import numpy as np
import time
import random
from itertools import combinations

from sklearn.preprocessing import OneHotEncoder, LabelEncoder, RobustScaler
from sklearn.compose import make_column_transformer
from sklearn.metrics import make_scorer, log_loss
from sklearn.model_selection import StratifiedKFold, cross_validate
from sklearn.inspection import permutation_importance
from sklearn.feature_selection import RFECV, mutual_info_classif
from sklearn.base import BaseEstimator, ClassifierMixin

from mlxtend.feature_selection import SequentialFeatureSelector as SFS
from concurrent.futures import ThreadPoolExecutor

from sklearn.ensemble import AdaBoostClassifier, BaggingClassifier, ExtraTreesClassifier, GradientBoostingClassifier, RandomForestClassifier, HistGradientBoostingClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.naive_bayes import GaussianNB
from sklearn.linear_model import LogisticRegression

from lightgbm import LGBMClassifier
from xgboost import XGBClassifier
from catboost import CatBoostClassifier

import tensorflow as tf

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, BatchNormalization
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.utils import to_categorical

import warnings
from pprint import pprint
import os

pd.set_option('display.max_columns', None)
warnings.filterwarnings('ignore')

experiment_name = 'mutual_information'

# Set seeds for reproducibility
np.random.seed(42)
tf.random.set_seed(42)
random.seed(42)

In [2]:
train = pd.read_csv(r'.\train.csv')
test = pd.read_csv(r'.\test.csv')

original = pd.read_csv(r'.\cirrhosis.csv')
original.dropna(inplace=True)
train.head(3)

id  N_Days             Drug    Age Sex Ascites Hepatomegaly Spiders Edema  \
0   0     999  D-penicillamine  21532   M       N            N       N     N   
1   1    2574          Placebo  19237   F       N            N       N     N   
2   2    3428          Placebo  13727   F       N            Y       Y     Y   

   Bilirubin  Cholesterol  Albumin  Copper  Alk_Phos    SGOT  Tryglicerides  \
0        2.3        316.0     3.35   172.0    1601.0  179.80           63.0   
1        0.9        364.0     3.54    63.0    1440.0  134.85           88.0   
2        3.3        299.0     3.55   131.0    1029.0  119.35           50.0   

   Platelets  Prothrombin  Stage Status  
0      394.0          9.7    3.0      D  
1      361.0         11.0    3.0      C  
2      199.0         11.7    4.0      D

In [3]:
train = pd.concat([train, original], axis=0)
train.shape

(8181, 21)

In [4]:
train.tail()

id  N_Days             Drug    Age Sex Ascites Hepatomegaly Spiders  \
307 NaN    1153  D-penicillamine  22347   F       N            Y       N   
308 NaN     994          Placebo  21294   F       N            N       N   
309 NaN     939  D-penicillamine  22767   F       N            N       N   
310 NaN     839  D-penicillamine  13879   F       N            N       N   
311 NaN     788          Placebo  12109   F       N            N       Y   

    Edema  Bilirubin  Cholesterol  Albumin  Copper  Alk_Phos   SGOT  \
307     N        0.4        246.0     3.58    24.0     797.0   91.0   
308     N        0.4        260.0     2.75    41.0    1166.0   70.0   
309     N        1.7        434.0     3.35    39.0    1713.0  171.0   
310     N        2.0        247.0     3.16    69.0    1050.0  117.0   
311     N        6.4        576.0     3.79   186.0    2115.0  136.0   

     Tryglicerides  Platelets  Prothrombin  Stage Status     ID  
307          113.0      288.0         10.4    2.0      C  308.0  
308           82.0      231.0         10.8    2.0      C  309.0  
309          100.0      234.0         10.2    2.0      C  310.0  
310           88.0      335.0         10.5    2.0      C  311.0  
311          149.0      200.0         10.8    2.0      C  312.0

In [5]:
TARGET = 'Status'
binary_cols = ['Ascites', 'Hepatomegaly', 'Spiders']
categorical_cols = ['Drug', 'Sex', 'Stage', 'Edema']
drop_cols = ['id', TARGET, 'ID']

In [6]:
numerical_cols = train.drop(categorical_cols + binary_cols + drop_cols, axis=1).select_dtypes(include=np.number).columns
numerical_cols

Index(['N_Days', 'Age', 'Bilirubin', 'Cholesterol', 'Albumin', 'Copper',
       'Alk_Phos', 'SGOT', 'Tryglicerides', 'Platelets', 'Prothrombin'],
      dtype='object')

In [7]:
yes_no_mapping = {'Y': 1, 'N': 0}

for col in binary_cols:
    train[col] = train[col].map(yes_no_mapping)
    test[col] = test[col].map(yes_no_mapping)

# Feature Engineering

In [8]:
epsilon = 1e-10

def feat_engineering(df, numerical_features, binary_cols):
    df_new = df.copy()

    # Transformation of numerical features
    for feature in numerical_features:
        # Log transformation (add small value to avoid log(0))
        df_new[f"{feature}_log"] = np.log(df[feature] + 1e-10)

        # Square root transformation
        df_new[f"{feature}_sqrt"] = np.sqrt(df[feature])

        # Polynomial transformations
        df_new[f"{feature}_degree2"] = df[feature]**2
        df_new[f"{feature}_degree3"] = df[feature]**3

    # Pairwise numerical feature operations
    for i in range(len(numerical_features)):
        for j in range(i, len(numerical_features)):
            if i != j:
                feat1 = numerical_features[i]
                feat2 = numerical_features[j]

                # Multiplication
                df_new[f"{feat1}_x_{feat2}"] = df[feat1] * df[feat2]

                # Addition
                df_new[f"{feat1}_plus_{feat2}"] = df[feat1] + df[feat2]

                # Subtraction (both ways)
                df_new[f"{feat1}_minus_{feat2}"] = df[feat1] - df[feat2]
                df_new[f"{feat2}_minus_{feat1}"] = df[feat2] - df[feat1]

                # Ratio (both ways)
                df_new[f"{feat1}_div_{feat2}"] = df[feat1] / (df[feat2] + epsilon)
                df_new[f"{feat2}_div_{feat1}"] = df[feat2] / (df[feat1] + epsilon)

                # Mean
                df_new[f"Mean_{feat1}_{feat2}"] = df[[feat1, feat2]].mean(axis=1)

                # Standard Deviation
                df_new[f"Std_{feat1}_{feat2}"] = df[[feat1, feat2]].std(axis=1)

                # Percentage Sum (both ways)
                df_new[f"percent_sum_{feat1}_{feat2}"] = (df[feat1] / (df[feat1] + df[feat2] + epsilon)) * 100
                df_new[f"percent_sum_{feat2}_{feat1}"] = (df[feat2] / (df[feat1] + df[feat2] + epsilon)) * 100
                
                # Compare value of features
                df_new[f"{feat1}_gt_{feat2}"] = (df[feat1] > df[feat2]).astype(int)

    # Additional feature engineering for 3 numerical features
    for i in range(len(numerical_features)):
        for j in range(i+1, len(numerical_features)):
            for k in range(j+1, len(numerical_features)):
                feat1, feat2, feat3 = numerical_features[i], numerical_features[j], numerical_features[k]

                # Addition of two features and then subtraction a third
                df_new[f"{feat1}_plus_{feat2}_minus_{feat3}"] = df[feat1] + df[feat2] - df[feat3]
                df_new[f"{feat1}_plus_{feat3}_minus_{feat2}"] = df[feat1] + df[feat3] - df[feat2]
                df_new[f"{feat2}_plus_{feat3}_minus_{feat1}"] = df[feat2] + df[feat3] - df[feat1]

                # Addition of all three features
                df_new[f"{feat1}_plus_{feat2}_plus_{feat3}"] = df[feat1] + df[feat2] + df[feat3]

                # Addition of two features to then be subtracted from the third
                df_new[f"{feat1}_plus_{feat2}_sub_by_{feat3}"] = df[feat3] - (df[feat1] + df[feat2])
                df_new[f"{feat1}_plus_{feat3}_sub_by_{feat2}"] = df[feat2] - (df[feat1] + df[feat3])
                df_new[f"{feat2}_plus_{feat3}_sub_by_{feat1}"] = df[feat1] - (df[feat2] + df[feat3])

                # Multiplication of all three features
                df_new[f"{feat1}_x_{feat2}_x_{feat3}"] = df[feat1] * df[feat2] * df[feat3]

                # One feature divided by the sum of the other two features (three combinations)
                df_new[f"{feat1}_div_sum_of_{feat2}_and_{feat3}"] = df[feat1] / (df[feat2] + df[feat3] + epsilon)
                df_new[f"{feat2}_div_sum_of_{feat1}_and_{feat3}"] = df[feat2] / (df[feat1] + df[feat3] + epsilon)
                df_new[f"{feat3}_div_sum_of_{feat1}_and_{feat2}"] = df[feat3] / (df[feat1] + df[feat2] + epsilon)

                # One feature divided by the multiplication of the other two features (three combinations)
                df_new[f"{feat1}_div_prod_of_{feat2}_and_{feat3}"] = df[feat1] / (df[feat2] * df[feat3] + epsilon)
                df_new[f"{feat2}_div_prod_of_{feat1}_and_{feat3}"] = df[feat2] / (df[feat1] * df[feat3] + epsilon)
                df_new[f"{feat3}_div_prod_of_{feat1}_and_{feat2}"] = df[feat3] / (df[feat1] * df[feat2] + epsilon)

                # The mean of all three features
                df_new[f"Mean_of_{feat1}_{feat2}_{feat3}"] = df[[feat1, feat2, feat3]].mean(axis=1)

                # The standard deviation of all three features
                df_new[f"Std_of_{feat1}_{feat2}_{feat3}"] = df[[feat1, feat2, feat3]].std(axis=1)

    for col1, col2 in combinations(binary_cols, 2):
        df_new[f'{col1}_and_{col2}'] = df_new[col1] & df_new[col2]
        df_new[f'{col1}_or_{col2}'] = df_new[col1] | df_new[col2]
        df_new[f'{col1}_nor_{col2}'] = ~(df_new[col1] | df_new[col2])
        df_new[f'{col1}_xor_{col2}'] = df_new[col1] ^ df_new[col2]

    for col1, col2, col3 in combinations(binary_cols, 3):
        df_new[f'{col1}_and_{col2}_and_{col3}'] = df_new[col1] & df_new[col2] & df_new[col3]
        df_new[f'{col1}_or_{col2}_or_{col3}'] = df_new[col1] | df_new[col2] | df_new[col3]
        df_new[f'{col1}_nor_{col2}_nor_{col3}'] = ~(df_new[col1] | df_new[col2] | df_new[col3])
        df_new[f'{col1}_xor_{col2}_xor_{col3}'] = df_new[col1] ^ df_new[col2] ^ df_new[col3]

    # Domain Knowledge
    # Bilirubin
    df_new['Bilirubin_Risk_Level'] = pd.cut(df['Bilirubin'], bins=[0, 1.2, 2, np.inf], labels=['Normal', 'Elevated', 'Jaundice'], right=False)

    # Total Serum Cholesterol
    df_new['Cholesterol_Risk_Level'] = pd.cut(df['Cholesterol'], bins=[0, 200, 240, np.inf], labels=['Normal', 'Borderline', 'High'], right=False)

    # Albumin
    df_new['Albumin_Risk_Level'] = pd.cut(df['Albumin'], bins=[0, 3.4, 5.4, np.inf], labels=['Low', 'Normal', 'High'], right=False)

    # Copper
    df_new['Copper_Normal'] = ((df['Copper'] >= 62) & (df['Copper'] <= 140)).astype(int)
    df_new['Copper_High'] = (df['Copper'] > 140).astype(int)

    # Alkaline Phosphatase (Alk_Phos)
    df_new['Alk_Phos_Normal'] = ((df['Alk_Phos'] >= 44) & (df['Alk_Phos'] <= 147)).astype(int)
    df_new['Alk_Phos_High'] = (df['Alk_Phos'] > 147).astype(int)

    # SGOT
    df_new['SGOT_Normal'] = ((df['SGOT'] >= 8) & (df['SGOT'] <= 45)).astype(int)

    # Tryglicerides
    df_new['Tryglicerides_Normal'] = (df['Tryglicerides'] < 150).astype(int)
    df_new['Tryglicerides_Borderline'] = ((df['Tryglicerides'] >= 150) & (df['Tryglicerides'] < 200)).astype(int)
    df_new['Tryglicerides_High'] = ((df['Tryglicerides'] >= 200) & (df['Tryglicerides'] < 500)).astype(int)
    df_new['Tryglicerides_Very_High'] = (df['Tryglicerides'] >= 500).astype(int)

    # Platelets
    df_new['Platelets_Normal'] = ((df['Platelets'] >= 150000) & (df['Platelets'] <= 450000)).astype(int)
    df_new['Platelets_Low'] = (df['Platelets'] < 150000).astype(int)

    # Prothrombin
    df_new['Prothrombin_Normal'] = ((df['Prothrombin'] >= 11) & (df['Prothrombin'] <= 13.5)).astype(int)

    # Age Group
    df_new['Age_Group'] = pd.cut(df['Age'], bins=[0, 18 * 365.25, 60 * 365.25, np.inf], labels=['Pediatric', 'Adult', 'Senior'])

    return df_new

In [9]:
train = feat_engineering(train, numerical_cols, binary_cols)
test = feat_engineering(test, numerical_cols, binary_cols)
train.shape, test.shape

((8181, 3342), (5271, 3340))

### Checking that feature engineering did not break anything

In [10]:
missing_in_yes = set(train.columns) - set(test.columns)
missing_in_yes

{'ID', 'Status'}

In [11]:
len(train.drop(drop_cols, axis=1).columns)

3339

In [12]:
feateng_binary_cols = []
feateng_categorical_cols = []


# Loop through every column columns to separate binary and categorical
for col in train.drop(drop_cols, axis=1).columns:
    unique_values = train[col].nunique(dropna=False)
    if unique_values == 2:
        feateng_binary_cols.append(col)
    elif unique_values > 2 and unique_values < 10:
        feateng_categorical_cols.append(col)

feateng_numerical_cols = list(train.drop(feateng_categorical_cols + feateng_binary_cols + drop_cols, axis=1).select_dtypes(include=np.number).columns)
feateng_numerical_cols
len(feateng_numerical_cols), len(feateng_binary_cols), len(feateng_categorical_cols)

(3279, 56, 4)

In [13]:
print(len(feateng_binary_cols) + len(feateng_categorical_cols) + len(feateng_numerical_cols))

3339


In [14]:
yes = feateng_numerical_cols + feateng_binary_cols + feateng_categorical_cols
print(len(yes))
no = list(train.columns)
print(len(no))

missing_in_yes = set(no) - set(yes)
missing_in_yes

3339
3342


{'ID', 'Status', 'id'}

In [15]:
if 'id' in test.columns:
    print('Yes')

Yes


# Preprocess Data

In [16]:
transformer = make_column_transformer(
    (OneHotEncoder(sparse=False, handle_unknown='infrequent_if_exist', drop='if_binary'), feateng_binary_cols),
    (OneHotEncoder(sparse=False, handle_unknown='infrequent_if_exist'), feateng_categorical_cols),
    (RobustScaler(), feateng_numerical_cols),
    remainder='passthrough')

df_to_ohe = train.drop(drop_cols, axis=1)
test = test.drop('id', axis=1)

transformed = transformer.fit_transform(df_to_ohe)

# Get the transformed feature names
transformed_feat_names = [name.split('__')[-1] for name in transformer.get_feature_names_out()]

# Create DataFrame of the transformed features
df_to_ohe_transformed = pd.DataFrame(transformed, columns=transformed_feat_names)
df_to_ohe_transformed.sample(3)

Drug_Placebo  Sex_M  Ascites_1  Hepatomegaly_1  Spiders_1  \
2464           0.0    0.0        0.0             1.0        0.0   
7286           0.0    0.0        0.0             1.0        0.0   
3862           1.0    0.0        0.0             1.0        0.0   

      N_Days_gt_Cholesterol_1  N_Days_gt_Copper_1  N_Days_gt_Alk_Phos_1  \
2464                      1.0                 1.0                   1.0   
7286                      1.0                 1.0                   0.0   
3862                      1.0                 1.0                   0.0   

      N_Days_gt_SGOT_1  N_Days_gt_Tryglicerides_1  N_Days_gt_Platelets_1  \
2464               1.0                        1.0                    1.0   
7286               1.0                        1.0                    1.0   
3862               1.0                        1.0                    1.0   

      Age_gt_Alk_Phos_1  Bilirubin_gt_Albumin_1  Bilirubin_gt_Copper_1  \
2464                1.0                     1.0                    0.0   
7286                1.0                     0.0                    0.0   
3862                1.0                     0.0                    0.0   

      Bilirubin_gt_Prothrombin_1  Cholesterol_gt_Copper_1  \
2464                         1.0                      1.0   
7286                         0.0                      1.0   
3862                         0.0                      1.0   

      Cholesterol_gt_Alk_Phos_1  Cholesterol_gt_SGOT_1  \
2464                        0.0                    1.0   
7286                        0.0                    1.0   
3862                        0.0                    1.0   

      Cholesterol_gt_Tryglicerides_1  Cholesterol_gt_Platelets_1  \
2464                             1.0                         1.0   
7286                             1.0                         1.0   
3862                             1.0                         1.0   

      Copper_gt_Alk_Phos_1  Copper_gt_SGOT_1  Copper_gt_Tryglicerides_1  \
2464                   0.0               0.0                        0.0   
7286                   0.0               0.0                        0.0   
3862                   0.0               0.0                        0.0   

      Copper_gt_Platelets_1  Copper_gt_Prothrombin_1  \
2464                    0.0                      1.0   
7286                    0.0                      1.0   
3862                    0.0                      1.0   

      Alk_Phos_gt_Tryglicerides_1  Alk_Phos_gt_Platelets_1  \
2464                          1.0                      1.0   
7286                          1.0                      1.0   
3862                          1.0                      1.0   

      SGOT_gt_Tryglicerides_1  SGOT_gt_Platelets_1  \
2464                      1.0                  1.0   
7286                      1.0                  0.0   
3862                      1.0                  0.0   

      Tryglicerides_gt_Platelets_1  Ascites_and_Hepatomegaly_1  \
2464                           0.0                         0.0   
7286                           0.0                         0.0   
3862                           0.0                         0.0   

      Ascites_or_Hepatomegaly_1  Ascites_nor_Hepatomegaly_-1  \
2464                        1.0                          0.0   
7286                        1.0                          0.0   
3862                        1.0                          0.0   

      Ascites_xor_Hepatomegaly_1  Ascites_and_Spiders_1  Ascites_or_Spiders_1  \
2464                         1.0                    0.0                   0.0   
7286                         1.0                    0.0                   0.0   
3862                         1.0                    0.0                   0.0   

      Ascites_nor_Spiders_-1  Ascites_xor_Spiders_1  \
2464                     1.0                    0.0   
7286                     1.0                    0.0   
3862                     1.0                    0.0   

      Hepatomegaly_and_

In [17]:
transformed_new_data = transformer.transform(test)

# Create DataFrame of the transformed features
test_transformed = pd.DataFrame(transformed_new_data, columns=transformed_feat_names)
test_transformed.sample(3)

Drug_Placebo  Sex_M  Ascites_1  Hepatomegaly_1  Spiders_1  \
2733           1.0    0.0        0.0             1.0        0.0   
2078           0.0    0.0        0.0             1.0        1.0   
5228           1.0    0.0        0.0             0.0        1.0   

      N_Days_gt_Cholesterol_1  N_Days_gt_Copper_1  N_Days_gt_Alk_Phos_1  \
2733                      1.0                 1.0                   0.0   
2078                      1.0                 1.0                   1.0   
5228                      1.0                 1.0                   1.0   

      N_Days_gt_SGOT_1  N_Days_gt_Tryglicerides_1  N_Days_gt_Platelets_1  \
2733               1.0                        1.0                    1.0   
2078               1.0                        1.0                    1.0   
5228               1.0                        1.0                    1.0   

      Age_gt_Alk_Phos_1  Bilirubin_gt_Albumin_1  Bilirubin_gt_Copper_1  \
2733                1.0                     0.0                    0.0   
2078                1.0                     0.0                    0.0   
5228                1.0                     0.0                    0.0   

      Bilirubin_gt_Prothrombin_1  Cholesterol_gt_Copper_1  \
2733                         0.0                      1.0   
2078                         0.0                      1.0   
5228                         0.0                      1.0   

      Cholesterol_gt_Alk_Phos_1  Cholesterol_gt_SGOT_1  \
2733                        0.0                    1.0   
2078                        0.0                    1.0   
5228                        0.0                    1.0   

      Cholesterol_gt_Tryglicerides_1  Cholesterol_gt_Platelets_1  \
2733                             1.0                         1.0   
2078                             1.0                         1.0   
5228                             1.0                         1.0   

      Copper_gt_Alk_Phos_1  Copper_gt_SGOT_1  Copper_gt_Tryglicerides_1  \
2733                   0.0               1.0                        1.0   
2078                   0.0               0.0                        0.0   
5228                   0.0               1.0                        1.0   

      Copper_gt_Platelets_1  Copper_gt_Prothrombin_1  \
2733                    1.0                      1.0   
2078                    0.0                      1.0   
5228                    0.0                      1.0   

      Alk_Phos_gt_Tryglicerides_1  Alk_Phos_gt_Platelets_1  \
2733                          1.0                      1.0   
2078                          1.0                      1.0   
5228                          1.0                      1.0   

      SGOT_gt_Tryglicerides_1  SGOT_gt_Platelets_1  \
2733                      0.0                  0.0   
2078                      0.0                  0.0   
5228                      1.0                  0.0   

      Tryglicerides_gt_Platelets_1  Ascites_and_Hepatomegaly_1  \
2733                           0.0                         0.0   
2078                           0.0                         0.0   
5228                           0.0                         0.0   

      Ascites_or_Hepatomegaly_1  Ascites_nor_Hepatomegaly_-1  \
2733                        1.0                          0.0   
2078                        1.0                          0.0   
5228                        0.0                          1.0   

      Ascites_xor_Hepatomegaly_1  Ascites_and_Spiders_1  Ascites_or_Spiders_1  \
2733                         1.0                    0.0                   0.0   
2078                         1.0                    0.0                   1.0   
5228                         0.0                    0.0                   1.0   

      Ascites_nor_Spiders_-1  Ascites_xor_Spiders_1  \
2733                     1.0                    0.0   
2078                     0.0                    1.0   
5228                     0.0                    1.0   

      Hepatomegaly_and_

In [18]:
encoded_binary_cols = []
encoded_categorical_cols = []


# Loop through every column columns to separate binary and categorical
for col in df_to_ohe_transformed.columns:
    unique_values = df_to_ohe_transformed[col].nunique(dropna=False)
    if unique_values == 2:
        encoded_binary_cols.append(col)
    elif unique_values > 2 and unique_values < 10:
        encoded_categorical_cols.append(col)

encoded_numerical_cols = list(df_to_ohe_transformed.drop(encoded_categorical_cols + encoded_binary_cols, axis=1).select_dtypes(include=np.number).columns)
encoded_numerical_cols
len(encoded_numerical_cols), len(encoded_binary_cols), len(encoded_categorical_cols)

(3279, 69, 0)

In [19]:
# # Temporarily adjust the display.max_rows setting to display all rows
# # Get the features and their nunique for confirmation
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):
#     listing = str(df_to_ohe_transformed.nunique().sort_values(ascending=False))
#     with open('columns.txt', 'w') as f:
#         f.write(listing)

In [20]:
label_encoder = LabelEncoder()

label_encoder.fit(train[TARGET])

df_to_ohe_transformed[TARGET] = label_encoder.transform(train[TARGET])

df_to_ohe_transformed.head()

Drug_Placebo  Sex_M  Ascites_1  Hepatomegaly_1  Spiders_1  \
0           0.0    1.0        0.0             0.0        0.0   
1           1.0    0.0        0.0             0.0        0.0   
2           1.0    0.0        0.0             1.0        1.0   
3           1.0    0.0        0.0             0.0        0.0   
4           1.0    0.0        0.0             1.0        0.0   

   N_Days_gt_Cholesterol_1  N_Days_gt_Copper_1  N_Days_gt_Alk_Phos_1  \
0                      1.0                 1.0                   0.0   
1                      1.0                 1.0                   1.0   
2                      1.0                 1.0                   1.0   
3                      1.0                 1.0                   1.0   
4                      1.0                 1.0                   0.0   

   N_Days_gt_SGOT_1  N_Days_gt_Tryglicerides_1  N_Days_gt_Platelets_1  \
0               1.0                        1.0                    1.0   
1               1.0                        1.0                    1.0   
2               1.0                        1.0                    1.0   
3               1.0                        1.0                    1.0   
4               1.0                        1.0                    1.0   

   Age_gt_Alk_Phos_1  Bilirubin_gt_Albumin_1  Bilirubin_gt_Copper_1  \
0                1.0                     0.0                    0.0   
1                1.0                     0.0                    0.0   
2                1.0                     0.0                    0.0   
3                1.0                     0.0                    0.0   
4                1.0                     0.0                    0.0   

   Bilirubin_gt_Prothrombin_1  Cholesterol_gt_Copper_1  \
0                         0.0                      1.0   
1                         0.0                      1.0   
2                         0.0                      1.0   
3                         0.0                      1.0   
4                         0.0                      1.0   

   Cholesterol_gt_Alk_Phos_1  Cholesterol_gt_SGOT_1  \
0                        0.0                    1.0   
1                        0.0                    1.0   
2                        0.0                    1.0   
3                        0.0                    1.0   
4                        0.0                    1.0   

   Cholesterol_gt_Tryglicerides_1  Cholesterol_gt_Platelets_1  \
0                             1.0                         0.0   
1                             1.0                         1.0   
2                             1.0                         1.0   
3                             1.0                         0.0   
4                             1.0                         1.0   

   Copper_gt_Alk_Phos_1  Copper_gt_SGOT_1  Copper_gt_Tryglicerides_1  \
0                   0.0               0.0                        1.0   
1                   0.0               0.0                        0.0   
2                   0.0               1.0                        1.0   
3                   0.0               0.0                        0.0   
4                   0.0               0.0                        0.0   

   Copper_gt_Platelets_1  Copper_gt_Prothrombin_1  \
0                    0.0                      1.0   
1                    0.0                      1.0   
2                    0.0                      1.0   
3                    0.0                      1.0   
4                    0.0                      1.0   

   Alk_Phos_gt_Tryglicerides_1  Alk_Phos_gt_Platelets_1  \
0                          1.0                      1.0   
1                          1.0                      1.0   
2                          1.0                      1.0   
3                          1.0                      1.0   
4                          1.0                      1.0   

   SGOT_gt_Tryglicerides_1  SGOT_gt_Platelets_1  Tryglicerides_gt_Platelets_1  \
0                      1.0                  0.0             

In [21]:
# Convert object type columns back to numeric if they were originally numeric
for col in df_to_ohe_transformed.columns:
    if df_to_ohe_transformed[col].dtype == 'object':
        df_to_ohe_transformed[col] = pd.to_numeric(df_to_ohe_transformed[col], errors='coerce')

# Check the first few rows of the DataFrame
df_to_ohe_transformed.head()

Drug_Placebo  Sex_M  Ascites_1  Hepatomegaly_1  Spiders_1  \
0           0.0    1.0        0.0             0.0        0.0   
1           1.0    0.0        0.0             0.0        0.0   
2           1.0    0.0        0.0             1.0        1.0   
3           1.0    0.0        0.0             0.0        0.0   
4           1.0    0.0        0.0             1.0        0.0   

   N_Days_gt_Cholesterol_1  N_Days_gt_Copper_1  N_Days_gt_Alk_Phos_1  \
0                      1.0                 1.0                   0.0   
1                      1.0                 1.0                   1.0   
2                      1.0                 1.0                   1.0   
3                      1.0                 1.0                   1.0   
4                      1.0                 1.0                   0.0   

   N_Days_gt_SGOT_1  N_Days_gt_Tryglicerides_1  N_Days_gt_Platelets_1  \
0               1.0                        1.0                    1.0   
1               1.0                        1.0                    1.0   
2               1.0                        1.0                    1.0   
3               1.0                        1.0                    1.0   
4               1.0                        1.0                    1.0   

   Age_gt_Alk_Phos_1  Bilirubin_gt_Albumin_1  Bilirubin_gt_Copper_1  \
0                1.0                     0.0                    0.0   
1                1.0                     0.0                    0.0   
2                1.0                     0.0                    0.0   
3                1.0                     0.0                    0.0   
4                1.0                     0.0                    0.0   

   Bilirubin_gt_Prothrombin_1  Cholesterol_gt_Copper_1  \
0                         0.0                      1.0   
1                         0.0                      1.0   
2                         0.0                      1.0   
3                         0.0                      1.0   
4                         0.0                      1.0   

   Cholesterol_gt_Alk_Phos_1  Cholesterol_gt_SGOT_1  \
0                        0.0                    1.0   
1                        0.0                    1.0   
2                        0.0                    1.0   
3                        0.0                    1.0   
4                        0.0                    1.0   

   Cholesterol_gt_Tryglicerides_1  Cholesterol_gt_Platelets_1  \
0                             1.0                         0.0   
1                             1.0                         1.0   
2                             1.0                         1.0   
3                             1.0                         0.0   
4                             1.0                         1.0   

   Copper_gt_Alk_Phos_1  Copper_gt_SGOT_1  Copper_gt_Tryglicerides_1  \
0                   0.0               0.0                        1.0   
1                   0.0               0.0                        0.0   
2                   0.0               1.0                        1.0   
3                   0.0               0.0                        0.0   
4                   0.0               0.0                        0.0   

   Copper_gt_Platelets_1  Copper_gt_Prothrombin_1  \
0                    0.0                      1.0   
1                    0.0                      1.0   
2                    0.0                      1.0   
3                    0.0                      1.0   
4                    0.0                      1.0   

   Alk_Phos_gt_Tryglicerides_1  Alk_Phos_gt_Platelets_1  \
0                          1.0                      1.0   
1                          1.0                      1.0   
2                          1.0                      1.0   
3                          1.0                      1.0   
4                          1.0                      1.0   

   SGOT_gt_Tryglicerides_1  SGOT_gt_Platelets_1  Tryglicerides_gt_Platelets_1  \
0                      1.0                  0.0             

In [22]:
df_to_ohe_transformed.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8181 entries, 0 to 8180
Columns: 3349 entries, Drug_Placebo to Status
dtypes: float64(3348), int32(1)
memory usage: 209.0 MB


In [23]:
test_transformed.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5271 entries, 0 to 5270
Columns: 3348 entries, Drug_Placebo to Platelets_Low
dtypes: float64(3348)
memory usage: 134.6 MB


# Feature Selection

### Remove highly correlated features

- Spearman Correlation

Dealing with continuous variables that are not normally distributed (and hence RobustScaler) and binary variables, Spearman's rank correlation coefficient might be the most appropriate. It does not assume a linear relationship or normality, making it suitable for a mixture of continuous (scaled) and binary variables.

In [24]:
# Remove correlated features (leaving just 1 of each pair)
# Leave features highly correlated with the target
df = df_to_ohe_transformed.drop(TARGET, axis=1)
correlation_matrix_spear = df.corr(method='spearman').abs()

# Select upper triangle of correlation matrix
upper_spear = correlation_matrix_spear.where(np.triu(np.ones(correlation_matrix_spear.shape), k=1).astype(bool))

# Find index of feature columns with correlation greater than a threshold (e.g., 0.9 in this case)
to_drop_spear = [column for column in upper_spear.columns if any(upper_spear[column] >= 0.9)]

# Drop features
df_reduced_spear = df_to_ohe_transformed.drop(to_drop_spear, axis=1)

# Get list of low correlation features excluding TARGET
low_corr_feats_spear = list(df_reduced_spear.drop(TARGET, axis=1).columns)

# Print the high correlation features effect
# Both pre and post drop dfs contain the TARGET
print(f"Dropped {len(to_drop_spear)} highly correlated features.\nOld Shape of the dataset was {df_to_ohe_transformed.shape}\nNew shape of the dataset is {df_reduced_spear.shape}")

Dropped 3074 highly correlated features.
Old Shape of the dataset was (8181, 3349)
New shape of the dataset is (8181, 275)


In [28]:
df_reduced_spear['Alk_Phos_div_sum_of_Copper_and_SGOT'].min(), df_reduced_spear['Alk_Phos_div_sum_of_Copper_and_SGOT'].max()

(-1.346605113899389, 29.72801621038076)

In [27]:
# Temporarily adjust the display.max_rows setting to display all rows
# Get the feature names to a text file
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    feats = str(low_corr_feats_spear)
    with open('low_corr_feats.txt', 'w') as f:
        f.write(feats)

### Mutual Information

In [29]:
# Generate a random feature
np.random.seed(5)
df_reduced_spear['random_control_feature'] = np.round(np.random.uniform(-2, 2, train.shape[0]), 6)
df_reduced_spear.shape

(8181, 276)

In [35]:
# Calculate mutual information - this can be memory and CPU intensive
# The plan is to remove any features that have mutual information less than random_feature because surely you cannot be important
mi_scores = mutual_info_classif(df_reduced_spear, df_reduced_spear[TARGET], discrete_features='auto', n_neighbors=15, copy=True, random_state=5)

# Make results easier to interpret by placing them in a DataFrame
mi_scores = pd.Series(mi_scores, name="MI Scores", index=df_reduced_spear.columns)
mi_scores = mi_scores.sort_values(ascending=False)

# Now you have the MI scores sorted from the most to the least informative
mi_scores.to_csv(f'{experiment_name}_15_mi_scores.csv')

In [37]:
# Read the CSV
mi_df = pd.read_csv('remove_highly_corr_feats_20_mi_scores.csv')

# Get the mi score for control feature
mi_threshold = mi_df.loc[mi_df['Feature'] == 'random_control_feature', 'Average'].iloc[0]

# Get the features above random_control_feature to move forward
mi_feats = mi_df[mi_df['Average'] > mi_threshold]['Feature'].tolist()
mi_feats

['Status',
 'N_Days_div_Bilirubin',
 'Bilirubin_x_Copper',
 'Bilirubin_plus_Prothrombin',
 'N_Days_div_Copper',
 'N_Days',
 'Bilirubin',
 'Bilirubin_div_Cholesterol',
 'Bilirubin_x_Alk_Phos',
 'Bilirubin_div_Tryglicerides',
 'N_Days_div_SGOT',
 'Bilirubin_x_Platelets',
 'Bilirubin_div_SGOT',
 'Copper',
 'Alk_Phos_div_prod_of_Bilirubin_and_Copper',
 'Copper_x_Alk_Phos',
 'Bilirubin_div_Alk_Phos',
 'N_Days_div_Tryglicerides',
 'Std_Bilirubin_Albumin',
 'N_Days_x_Platelets',
 'Alk_Phos',
 'Bilirubin_Risk_Level_Jaundice',
 'SGOT',
 'Cholesterol',
 'Platelets',
 'Cholesterol_div_Copper',
 'Age',
 'Copper_plus_SGOT_minus_Tryglicerides',
 'Platelets_div_sum_of_Bilirubin_and_Albumin',
 'Copper_minus_SGOT',
 'Age_x_SGOT',
 'Bilirubin_Risk_Level_Normal',
 'SGOT_x_Tryglicerides',
 'N_Days_div_Platelets',
 'N_Days_minus_Alk_Phos',
 'N_Days_x_Bilirubin',
 'Bilirubin_div_prod_of_N_Days_and_Copper',
 'Cholesterol_x_SGOT',
 'Bilirubin_div_prod_of_Cholesterol_and_SGOT',
 'N_Days_x_Bilirubin_x_Copper',


## Training Machine Learning Models

In [38]:
X = df_reduced_spear[mi_feats].drop(TARGET, axis=1)
y = df_reduced_spear[TARGET]
test_features = test_transformed[low_corr_feats_spear].copy()

sk = StratifiedKFold(n_splits=10, shuffle=True, random_state=5)

### Keras Model

In [39]:
class KerasClassifierWrapper(BaseEstimator, ClassifierMixin):
    def __init__(self, epochs=100, batch_size=32):
        self.epochs = epochs
        self.batch_size = batch_size
        self.model = self.create_model()

    def create_model(self):
        model = Sequential()
        model.add(Dense(128, input_dim=len(X.columns), activation='relu'))
        model.add(BatchNormalization())
        model.add(Dense(64, activation='relu'))
        model.add(BatchNormalization())
        model.add(Dense(32, activation='relu'))
        model.add(BatchNormalization())
        model.add(Dense(3, activation='softmax'))  # Output layer for 3 classes
        model.compile(optimizer='adam', 
                      loss='categorical_crossentropy', 
                      metrics=[tf.keras.metrics.CategoricalCrossentropy(name='log_loss')])
        return model

    def fit(self, X, y):
        # self.model = self.create_model()
        early_stopping = EarlyStopping(monitor='val_loss', patience=30, restore_best_weights=True, mode='min')
        reduce_LR = tf.keras.callbacks.ReduceLROnPlateau(monitor='val_loss', patience=5, min_lr=0.00001, factor=0.8)

        self.model.fit(X, to_categorical(y), 
                       epochs=self.epochs, 
                       batch_size=self.batch_size, 
                       verbose=0, 
                       validation_split=0.1, 
                       callbacks=[early_stopping, reduce_LR])
        return self

    def predict_proba(self, X):
        return self.model.predict(X)

    def score(self, X, y):
        y_pred = self.predict_proba(X)
        return -log_loss(to_categorical(y), y_pred)

In [40]:
# def create_model(): 
#     model = Sequential()
#     model.add(Dense(128, input_dim=len(X.columns), activation='relu'))
#     model.add(BatchNormalization())
#     model.add(Dense(64, activation='relu'))
#     model.add(BatchNormalization())
#     model.add(Dense(32, activation='relu'))
#     model.add(BatchNormalization())
#     model.add(Dense(3, activation='softmax'))  # Output layer for 3 classes

#     model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['categorical_crossentropy'])
#     return model

# def fit_predict(model, X_train, y_train, X_test):
#     early_stopping = EarlyStopping(monitor='val_loss', patience=30, restore_best_weights=True, mode='min')
#     reduce_LR = tf.keras.callbacks.ReduceLROnPlateau(monitor='val_loss', patience=5, min_lr=0.00001, factor=0.8)

#     model.fit(X_train, to_categorical(y_train), epochs=100, 
#               batch_size=32, verbose=0, validation_split=0.2, 
#               callbacks=[early_stopping, reduce_LR])
    
#     y_pred = model.predict(X_test)
    
#     return y_pred

# # Custom scorer function
# def custom_log_loss(y_true, y_pred):
#     return log_loss(to_categorical(y_true), y_pred)

# # Cross-validation
# log_loss_scores = []

# for train, test in sk.split(X, y):
#     model = create_model()
#     y_pred = fit_predict(model, X.iloc[train], y.iloc[train], X.iloc[test])
#     score = custom_log_loss(y.iloc[test], y_pred)
#     log_loss_scores.append(score)

# # Print the results
# print("Log Loss: %.2f (%.2f)" % (np.mean(log_loss_scores), np.std(log_loss_scores)))

### List of models

In [41]:
models = [
	# Ensemble and Tree Methods
	AdaBoostClassifier(random_state=5),
	BaggingClassifier(random_state=5),
	ExtraTreesClassifier(random_state=5),
	GradientBoostingClassifier(random_state=5),
	HistGradientBoostingClassifier(random_state=5),
	RandomForestClassifier(random_state=5),
    
	XGBClassifier(random_state=5),
	LGBMClassifier(n_jobs=-1, random_state=5),
	CatBoostClassifier(random_state=5, verbose=False, early_stopping_rounds=100),
    
	# Liner Models
    LogisticRegression(multi_class='multinomial', solver='lbfgs'),
    
	# Support Vector Machine
    SVC(probability=True),
    
	# KNeighbors & Naive Models
	KNeighborsClassifier(),
    GaussianNB(),
    
	# NeuralNet
	KerasClassifierWrapper(),
    ]

# # create table to compare MLA metrics
# MLA_columns = ['MLA Name', 'MLA Parameters', 'MLA Train Accuracy Mean', 'MLA Test Accuracy Mean', 'MLA Test Accuracy 3*STD', 'MLA Time']
# MLA_compare = pd.DataFrame(columns = MLA_columns)

### Cross-validation function

In [42]:
def evaluate_models(models, X, y, important_features, cv_split, experiment_name):
    # Create a DataFrame to store comparison results
    MLA_compare = pd.DataFrame(columns=['MLA Name', 
                                        'MLA Parameters', 
                                        'MLA Train Log Loss', 
                                        'MLA Test Log Loss', 
                                        'MLA Time'])
    
    def evaluate_model(alg, idx):
        MLA_name = alg.__class__.__name__
        features = important_features.get(MLA_name, [])

        if not features:
            return None

        # Perform cross-validation
        log_loss_scorer = make_scorer(log_loss, greater_is_better=False, needs_proba=True)
        
        cv_results = cross_validate(alg, X[features], y, 
                                    cv=cv_split, 
                                    scoring={'Log Loss': log_loss_scorer}, 
                                    return_train_score=True, 
                                    n_jobs=-1)

        # Format time
        mean_fit_time = cv_results['fit_time'].mean()
        minutes, seconds = divmod(mean_fit_time, 60)

        print(f'Done with {MLA_name}.')
        
        # Populate results
        return {
            'MLA Name': MLA_name,
            'MLA Parameters': str(alg.get_params()),
            'MLA Train Log Loss': -cv_results['train_Log Loss'].mean(),
            'MLA Test Log Loss': -cv_results['test_Log Loss'].mean(),
            'MLA Time': f"{int(minutes)} min {seconds:.2f} sec",
        }

    results_list = []

    # Use ThreadPoolExecutor for parallel execution
    with ThreadPoolExecutor(max_workers=10) as executor:
        futures = [executor.submit(evaluate_model, alg, idx) for idx, alg in enumerate(models)]
        for future in futures:
            result = future.result()
            if result:
                results_list.append(result)

    # Create a DataFrame from the list of dictionaries
    MLA_compare = pd.DataFrame(results_list)

    # Sort and save results
    MLA_compare.sort_values(by=['MLA Test Log Loss'], ascending=True, inplace=True)
    MLA_compare.to_csv(f'{experiment_name}_results.csv', index=False)

    return MLA_compare

# Usage:
# models = [list of your models]
# MLA_compare = evaluate_models(models, X, y, important_features, cv_split, 'experiment_name')

### Baseline Model

In [43]:
baseline_features = {}

for model in models:
    model_name = model.__class__.__name__

    baseline_features[model_name] = list(X.columns)

In [46]:
len(baseline_features['GaussianNB'])

233

In [48]:
# Set seeds for reproducibility
np.random.seed(42)
tf.random.set_seed(42)
random.seed(42)

baseline_models = evaluate_models(models, X, y, baseline_features, sk, f'{experiment_name}')
baseline_models

Done with AdaBoostClassifier.
Done with CatBoostClassifier.
Done with RandomForestClassifier.
Done with BaggingClassifier.
Done with LogisticRegression.
Done with LGBMClassifier.
Done with ExtraTreesClassifier.
Done with HistGradientBoostingClassifier.
Done with GradientBoostingClassifier.
Done with XGBClassifier.
Done with KNeighborsClassifier.
Done with GaussianNB.
Done with SVC.
Done with KerasClassifierWrapper.


MLA Name  \
3       GradientBoostingClassifier   
8               CatBoostClassifier   
7                   LGBMClassifier   
9               LogisticRegression   
10                             SVC   
13          KerasClassifierWrapper   
4   HistGradientBoostingClassifier   
6                    XGBClassifier   
5           RandomForestClassifier   
2             ExtraTreesClassifier   
0               AdaBoostClassifier   
1                BaggingClassifier   
11            KNeighborsClassifier   
12                      GaussianNB   

                                       MLA Parameters  MLA Train Log Loss  \
3   {'ccp_alpha': 0.0, 'criterion': 'friedman_mse'...            0.343838   
8   {'verbose': False, 'random_state': 5, 'early_s...            0.148346   
7   {'boosting_type': 'gbdt', 'class_weight': None...            0.102910   
9   {'C': 1.0, 'class_weight': None, 'dual': False...            0.454586   
10  {'C': 1.0, 'break_ties': False, 'cache_size': ...            0.476318   
13                  {'batch_size': 32, 'epochs': 100}            0.354754   
4   {'categorical_features': None, 'early_stopping...            0.057758   
6   {'objective': 'binary:logistic', 'use_label_en...            0.027688   
5   {'bootstrap': True, 'ccp_alpha': 0.0, 'class_w...            0.115611   
2   {'bootstrap': False, 'ccp_alpha': 0.0, 'class_...            0.000904   
0   {'algorithm': 'SAMME.R', 'base_estimator': Non...            1.047394   
1   {'base_estimator': None, 'bootstrap': True, 'b...            0.122640   
11  {'algorithm': 'auto', 'leaf_size': 30, 'metric...            0.327332   
12           {'priors': None, 'var_smoothing': 1e-09}            9.658723   

    MLA Test Log Loss          MLA Time  
3            0.457005   8 min 14.56 sec  
8            0.462545  10 min 16.92 sec  
7            0.482727   0 min 36.64 sec  
9            0.510243    0 min 2.13 sec  
10           0.516025   2 min 24.10 sec  
13           0.517807   1 min 49.21 sec  
4            0.523518    1 min 8.02 sec  
6            0.543456   5 min 27.38 sec  
5            0.560816   0 min 36.48 sec  
2            0.614141    0 min 9.51 sec  
0            1.049173   0 min 34.04 sec  
1            1.519326    1 min 6.63 sec  
11           2.683447    0 min 0.13 sec  
12           9.732832    0 min 0.31 sec

# Ensembling

In [ ]:
# def hill_climbing(x, y, x_test):
#     le = LabelEncoder()
#     y_encoded = le.fit_transform(y)
#     y_one_hot = pd.get_dummies(y_encoded)

#     # Evaluating out-of-fold predictions
#     scores = {}
#     for col in x.columns:
#         scores[col] = log_loss(y_one_hot, x[[col]])

#     # Sorting the model scores in ascending order
#     scores = {k: v for k, v in sorted(scores.items(), key=lambda item: item[1])}
#     print(scores)

#     # Sort x and x_test based on scores
#     x = x[list(scores.keys())]
#     x_test = x_test[list(scores.keys())]

#     # Initialize weights
#     weights = {col: 1 if i == 0 else 0 for i, col in enumerate(x.columns)}

#     STOP = False
#     current_best_ensemble = x.iloc[:,0]
#     current_best_test_ensemble = x_test.iloc[:,0]
#     MODELS = x.iloc[:,1:]
#     weight_range = np.arange(-0.5, 0.51, 0.01) 
#     history = [log_loss(y_one_hot, current_best_ensemble)]

#     while not STOP:
#         potential_new_best_cv_score = log_loss(y_one_hot, current_best_ensemble)
#         k_best, wgt_best = None, None
#         for k in MODELS:
#             for wgt in weight_range:
#                 potential_ensemble = (1 - wgt) * current_best_ensemble + wgt * MODELS[k]
#                 cv_score = log_loss(y_one_hot, potential_ensemble)
#                 if cv_score < potential_new_best_cv_score:
#                     potential_new_best_cv_score = cv_score
#                     k_best, wgt_best = k, wgt

#         if k_best is not None:
#             # Update weights
#             weights = {col: (1 - wgt_best) * weights[col] if col != k_best else wgt_best for col in weights}
#             current_best_ensemble = (1 - wgt_best) * current_best_ensemble + wgt_best * MODELS[k_best]
#             current_best_test_ensemble = (1 - wgt_best) * current_best_test_ensemble + wgt_best * x_test[k_best]
#             MODELS.drop(k_best, axis=1, inplace=True)
            
#             if MODELS.shape[1] == 0:
#                 STOP = True
#             history.append(potential_new_best_cv_score)
#         else:
#             STOP = True
        
#     hill_ens_pred = current_best_ensemble
#     hill_ens_pred_test = current_best_test_ensemble
    
#     return hill_ens_pred, hill_ens_pred_test, weights

In [ ]:
# model_scores = []
# model_fold_scores = []
# models_dict = {}

# for idx, model_name in enumerate(model_names):
    
#     pred_cols = [f"pred_{response_col}_{c}_{model_name}" for c in response_col_order]
    
#     print("="*25)
#     print(f"Starting training, validation and prediction for model {model_name} [MODEL {idx+1}/{len(model_names)}]")
#     print("="*25)
    
#     print("-"*25)
#     print(f"Training model:")
#     print("-"*25)
    
#     start_time = time.process_time()
    
#     trainer = KFoldTrainer(
#         seed = CFG.seed,
#         model_name = model_name,
#         model_params = model_params_dict[model_name],
#     )
#     # training
#     trainer.train_by_fold(df_combined, feature_names, verbose=True)
#     print("-"*25)
    
#     models_dict[model_name] = trainer.get_saved_models()
    
#     # validation
#     pred_train, metric, fold_metrics, mean_fold_metric, sd_fold_metric = \
#         trainer.get_oof_predictions_and_metric(df_combined, feature_names)
    
#     df_combined[pred_cols] = pred_train
    
#     for fold in range(CFG.n_folds):
#         print(f"LOSS for FOLD {fold}: {fold_metrics[fold]:6f}")
#     print()
#     print(f"OOF LOSS for {model_name}: {metric:.6f}")
#     print(f"Mean/SD LOSS for {model_name}: {mean_fold_metric:.6f} ± {sd_fold_metric:.6f}")
    
#     # for plotting later on
#     model_scores.append({
#         'model_name': model_name,
#         'score': metric,
#     })
#     model_fold_scores.extend([{
#         'model_name': model_name,
#         'fold': fold,
#         'score': fold_metrics[fold]
#     } for fold in range(CFG.n_folds)])
    
#     # prediction (test set)
#     print("-"*25)
#     print(f"Predicting test set with model:")
#     print("-"*25)
#     df_test[pred_cols] = trainer.predict(df_test, feature_names, verbose=True)
    
#     # cleanup
#     del trainer, pred_train, metric, fold_metrics, mean_fold_metric, sd_fold_metric
#     gc.collect()

In [ ]:
# Set seeds for reproducibility
np.random.seed(42)
tf.random.set_seed(42)
random.seed(42)

# hill_climb_scores = []
# hc_test_scores = []
# hill_climb_weights = []
# final_predictions = []
# final_hc_predictions = []
# avg_predictions_scores = []
# optuna_weights_scores = []
# stacked_scores = []
# optuna_weights_scores_stack = []

# labels = list(range(y.nunique()))

# for i, (train_index, test_index) in enumerate(sk.split(X, y)):
#     X_train, X_test = X.iloc[train_index], X.iloc[test_index]
#     y_train, y_test = y.iloc[train_index], y.iloc[test_index]

#     print(f'Fold {i+1}')
    
#     MLA_cv_train_preds = []
#     MLA_cv_preds = []
#     MLA_cv_preds_dict = {}
#     MLA_cv_preds_test_dict = {}
#     MLA_names = []
    
#     for alg in models:
#         MLA_name = alg.__class__.__name__
        
#         predictor = alg.fit(X_train, y_train)
#         pred_result = predictor.predict_proba(X_test)
#         test_result = predictor.predict_proba(test_features)

#         # MLA_cv_preds.append(pred_result)
#         # final_predictions.append(test_result)

#         # MLA_cv_preds_dict[MLA_name] = pred_result
#         # MLA_cv_preds_test_dict[MLA_name] = test_result

#         # Store each class's predictions separately
#         for class_index in range(pred_result.shape[1]):
#             class_name = f'{MLA_name}_class_{class_index}'
#             MLA_cv_preds_dict[class_name] = pred_result[:, class_index]
#             MLA_cv_preds_test_dict[class_name] = test_result[:, class_index]


#         MLA_names.append(MLA_name)

#         print(f'Done with {MLA_name}')

#     print(MLA_cv_preds_dict)
#     print(MLA_cv_preds_test_dict)
    
#     #################
#     ### Averaging ###
#     #################
#     avg_prediction = np.mean(MLA_cv_preds, axis=0)
#     avg_prediction_score = log_loss(y_test, avg_prediction)
#     avg_predictions_scores.append(avg_prediction_score)
#     print(f'The Fold {i+1} average prediction log loss is {avg_prediction_score}')

#     print(MLA_cv_preds_dict)
#     print(MLA_cv_preds_test_dict)

#     ##################
#     ### Hill Climb ###
#     ##################
#     hill_climb_pred, hill_climb_final_pred, hill_climb_weight = hill_climbing(pd.DataFrame(MLA_cv_preds_dict), y_test, pd.DataFrame(MLA_cv_preds_test_dict))
    
#     hill_climb_score = log_loss(y_test, hill_climb_pred)
#     # hc_test_score = mean_absolute_error(test_target, hill_climb_final_pred)
#     hill_climb_scores.append(hill_climb_score)
#     # hc_test_scores.append(hc_test_score)
#     final_hc_predictions.append(hill_climb_final_pred)
#     hill_climb_weights.append(hill_climb_weight)
    
#     print(f'The Fold {i+1} Hill Climb CV Log Loss Score is {hill_climb_score}')
#     # print(f'The Fold {i+1} Hill Climb Actual Data Score is {hc_test_score}')
#     print(f'The Fold {i+1} weight are {hill_climb_weight}')

#     print()

# print()
# print(f'The average prediction CV log loss is ==> {np.mean(avg_predictions_scores)}')
# print(f'The Hill Climbing CV log loss is ==> {np.mean(hill_climb_scores)}')
# # print(f'The Hill Climbing Test CV score is ==> {np.mean(hc_test_scores)}')
# print(f'The Hill Climbing weights are ==> {hill_climb_weights}')

In [ ]:
# # Set seeds for reproducibility
# np.random.seed(42)
# tf.random.set_seed(42)
# random.seed(42)

# ensemble_log_losses = []
# fold_weights = []  # To store weights for each fold
# weight_range = np.arange(-0.5, 0.51, 0.01)

# for train_index, test_index in sk.split(X, y):
#     X_train, X_test = X.iloc[train_index], X.iloc[test_index]
#     y_train, y_test = y.iloc[train_index], y.iloc[test_index]

#     # Storing predictions
#     model_predictions_train = {}
#     model_predictions_test = {}

#     for model in models:
#         model_name = model.__class__.__name__
#         model.fit(X_train, y_train)
#         model_predictions_train[model_name] = model.predict_proba(X_test)
#         model_predictions_test[model_name] = model.predict_proba(X_test)
#         print(f'Done with {model_name}', end='\n')

#     # Initialize ensemble with the first model
#     first_model_name = next(iter(model_predictions_train.keys()))
#     current_best_ensemble = model_predictions_train[first_model_name]
#     current_best_test_ensemble = model_predictions_test[first_model_name]

#     # Initialize weights
#     model_weights = {model_name: 0 for model_name in model_predictions_train.keys()}
#     model_weights[first_model_name] = 1.0

#     # Remove the first model from the list
#     MODELS = list(model_predictions_train.keys())[1:]
#     STOP = False
#     history = [log_loss(y_test, current_best_ensemble)]
#     fold_weights_current = [model_weights.copy()]

#     while not STOP:
#         potential_new_best_cv_score = log_loss(y_test, current_best_ensemble)
#         k_best, wgt_best = None, None
#         for k in MODELS:
#             for wgt in weight_range:
#                 potential_ensemble = (1 - wgt) * current_best_ensemble + wgt * model_predictions_train[k]
#                 cv_score = log_loss(y_test, potential_ensemble)
#                 if cv_score < potential_new_best_cv_score:
#                     potential_new_best_cv_score = cv_score
#                     k_best, wgt_best = k, wgt

#         if k_best is not None:
#             # Update ensemble
#             current_best_ensemble = (1 - wgt_best) * current_best_ensemble + wgt_best * model_predictions_train[k_best]
#             current_best_test_ensemble = (1 - wgt_best) * current_best_test_ensemble + wgt_best * model_predictions_test[k_best]
            
#             # Update weights
#             model_weights = {model_name: (1 - wgt_best) * model_weights[model_name] if model_name != k_best else wgt_best for model_name in model_weights}
#             fold_weights_current.append(model_weights.copy())
#             MODELS.remove(k_best)

#             if len(MODELS) == 0:
#                 STOP = True
#             history.append(potential_new_best_cv_score)
#         else:
#             STOP = True

#     # Calculate log loss for the optimized ensemble on the test set and store weights
#     loss = log_loss(y_test, current_best_ensemble)
#     print(loss)
#     ensemble_log_losses.append(loss)
#     fold_weights.append(fold_weights_current[-1])  # Store final weights of this fold

# # Average log loss across all folds
# average_log_loss = np.mean(ensemble_log_losses)
# print(f"Ensemble Average Log Loss: {average_log_loss}")
# print("Weights per fold:", fold_weights)

In [ ]:
# # Set seeds for reproducibility
# np.random.seed(42)
# tf.random.set_seed(42)
# random.seed(42)

# ensemble_log_losses = []
# weight_range = np.arange(-0.5, 0.6, 0.01)

# for train_index, test_index in sk.split(X, y):
#     X_train, X_test = X.iloc[train_index], X.iloc[test_index]
#     y_train, y_test = y.iloc[train_index], y.iloc[test_index]

#     # Storing predictions and calculating individual log losses
#     model_predictions = {}
#     model_log_losses = {}

#     for model in models:
#         model_name = model.__class__.__name__
#         model.fit(X_train, y_train)
#         probas = model.predict_proba(X_test)
#         model_predictions[model_name] = probas
#         model_log_losses[model_name] = log_loss(y_test, probas)
#         print(f'Done with {model_name}', end='\n')

#     # Sorting models by their log loss
#     sorted_models = sorted(model_log_losses, key=model_log_losses.get)

#     # Initialize model weights: best model gets weight 1, others get 0
#     model_weights = {model: 1 if model == sorted_models[0] else 0 for model in model_log_losses.keys()}

#     # Hill Climbing for optimizing weights
#     best_loss = model_log_losses[sorted_models[0]]
#     for model_name in model_weights.keys():
#         for wgt in weight_range:
#             temp_weights = model_weights.copy()
#             temp_weights[model_name] = wgt
#             remaining_weight = 1 - wgt
#             for other_model in temp_weights:
#                 if other_model != model_name:
#                     temp_weights[other_model] = remaining_weight / (len(models) - 1)

#             combined_preds = np.zeros_like(next(iter(model_predictions.values())))
#             for m_name, m_probas in model_predictions.items():
#                 combined_preds += temp_weights[m_name] * m_probas

#             current_loss = log_loss(y_test, combined_preds / combined_preds.sum(axis=1, keepdims=True))
#             if current_loss < best_loss:
#                 best_loss = current_loss
#                 model_weights = temp_weights.copy()

#     # Calculate log loss with optimized weights
#     optimized_preds = np.zeros_like(next(iter(model_predictions.values())))
#     for m_name, m_probas in model_predictions.items():
#         optimized_preds += model_weights[m_name] * m_probas

#     loss = log_loss(y_test, optimized_preds / optimized_preds.sum(axis=1, keepdims=True))
#     ensemble_log_losses.append(loss)

# # Average log loss across all folds
# average_log_loss = np.mean(ensemble_log_losses)
# print(f"Ensemble Average Log Loss: {average_log_loss}")
# print(sum(model_weights.values()))

In [ ]:
# # Set seeds for reproducibility
# np.random.seed(42)
# tf.random.set_seed(42)
# random.seed(42)

# ensemble_log_losses = []
# weight_range = np.arange(-0.5, 0.6, 0.01)

# for train_index, test_index in sk.split(X, y):
#     X_train, X_test = X.iloc[train_index], X.iloc[test_index]
#     y_train, y_test = y.iloc[train_index], y.iloc[test_index]

#     # Storing predictions and calculating individual log losses
#     model_predictions = {}
#     model_log_losses = {}

#     for model in models:
#         model_name = model.__class__.__name__
#         model.fit(X_train, y_train)
#         probas = model.predict_proba(X_test)
#         model_predictions[model_name] = probas
#         model_log_losses[model_name] = log_loss(y_test, probas)
#         print(f'Done with {model_name}', end='\n')

#     # Sorting models by their log loss
#     sorted_models = sorted(model_log_losses, key=model_log_losses.get)

#     # Initialize model weights: best model gets weight 1, others get 0
#     model_weights = {model: 1 if model == sorted_models[0] else 0 for model in model_log_losses.keys()}

#     # Hill Climbing for optimizing weights
#     best_loss = model_log_losses[sorted_models[0]]
#     for model_name, probas in model_predictions.items():
#         for wgt in weight_range:
#             combined_preds = np.zeros_like(probas)
#             for m_name, m_probas in model_predictions.items():
#                 weight = wgt if m_name == model_name else model_weights[m_name]
#                 combined_preds += weight * m_probas

#             current_loss = log_loss(y_test, combined_preds / combined_preds.sum(axis=1, keepdims=True))
#             if current_loss < best_loss:
#                 best_loss = current_loss
#                 model_weights[model_name] = wgt

#     # Calculate log loss with optimized weights
#     optimized_preds = np.zeros_like(probas)
#     for m_name, m_probas in model_predictions.items():
#         optimized_preds += model_weights[m_name] * m_probas

#     loss = log_loss(y_test, optimized_preds / optimized_preds.sum(axis=1, keepdims=True))
#     ensemble_log_losses.append(loss)

# # Average log loss across all folds
# average_log_loss = np.mean(ensemble_log_losses)
# print(f"Ensemble Average Log Loss: {average_log_loss}")
# print(sum(model_weights.values()))